In [1]:
import pandas as pd

import torch
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence

import torch.nn as nn
import torch.nn.functional as F
from torch.optim import Adam

from sklearn.model_selection import train_test_split
from matplotlib import pyplot as plt

from tqdm import tqdm
# from tqdm.notebook import tqdm

from ray import tune, train
from ray.tune import CLIReporter
from ray.tune.schedulers import ASHAScheduler

In [2]:
# ! pip install ray[tune]

In [3]:
# ! pip install ax-platform

# 1.观察数据

In [4]:
# df = pd.read_csv('deep-learning-for-msc-202324/train/1A0A_3_A_train.csv')
# df

In [5]:
# seqs_test = pd.read_csv('deep-learning-for-msc-202324/seqs_test.csv')
# seqs_test

In [6]:
# seqs_train = pd.read_csv('deep-learning-for-msc-202324/seqs_train.csv')
# seqs_train

In [7]:
# labels_train = pd.read_csv('deep-learning-for-msc-202324/labels_train.csv')
# labels_train

# 2.数据准备和数据加载器(DataLoader)
从给定的CSV文件中加载序列数据和PSSM数据，并将它们转换为PyTorch张量。这涉及到读取文件，处理数据格式，并应用适当的编码（如one-hot编码）来表示蛋白质序列和二级结构标签（H/E/C）。
实现一个PyTorch Dataset类，能够处理蛋白质序列和PSSM数据，以及相应的二级结构标签。
创建一个PyTorch DataLoader来批量地、有效地迭代这些数据，为训练模型做准备。


In [8]:
def collate_fn_with_pssm(batch):
    """
    Custom collate_fn to pad sequences, labels, and PSSM profiles
    用于处理批处理中的填充
    这个函数是用来处理数据批处理的填充问题的。当你从DataLoader中获取一个批次的数据时，这个函数将自动被调用以处理数据的填充，确保每个批次中所有序列的长度相同。
    :param batch: A list of tuples, each containing a sequence tensor, a label tensor, and a PSSM tensor
    :type batch: 
    :return: 
    :rtype: 
    """
    sequences, labels, pssms = zip(*batch)  # 将批次中的数据解包成序列、标签和PSSM数据。

    # pad_sequence函数用于填充序列和PSSM数据，以确保批次中的所有项长度一致。
    # batch_first=True参数确保填充后的数据第一个维度是批次大小。
    sequences_padded = pad_sequence(sequences, batch_first=True)
    labels_padded = pad_sequence(labels, batch_first=True, padding_value=-1)  # 使用-1作为填充值 对于分类任务中的忽略标签非常有用
    pssms_padded = pad_sequence(pssms, batch_first=True)

    return sequences_padded, labels_padded, pssms_padded

In [9]:
class ProteinDatasetWithPSSM(Dataset):
    """
    用于加载蛋白质序列、PSSM配置文件和二级结构数据的自定义数据集，
    支持基于PDB_ID列表的数据分割。
    """

    def __init__(self, seqs_path, labels_path, pssm_folder, pdb_ids):
        """
        初始化数据集
        :param seqs_path: 氨基酸序列数据的文件路径
        :param labels_path: 二级结构标签数据的文件路径
        :param pssm_folder: PSSM数据文件所在的文件夹路径
        :param pdb_ids: 一个PDB_ID列表，指定应该包含在数据集中的样本
        """
        # 加载序列数据和标签数据
        self.seqs_data = pd.read_csv(seqs_path)
        self.labels_data = None if labels_path is None else pd.read_csv(labels_path)

        # 只保留指定的pdb_ids样本
        self.seqs_data = self.seqs_data[self.seqs_data['PDB_ID'].isin(pdb_ids)]
        if self.labels_data is not None:
            self.labels_data = self.labels_data[self.labels_data['PDB_ID'].isin(pdb_ids)]


        self.pssm_folder = pssm_folder

    def __len__(self):
        return len(self.seqs_data)

    def __getitem__(self, idx):
        pdb_id = self.seqs_data.iloc[idx]['PDB_ID']  # 检索出当前样本的PDB_ID
        sequence = self.seqs_data.iloc[idx]['SEQUENCE']  # 获取当前样本的氨基酸序列
        seq_tensor = self.sequence_to_tensor(sequence)  #将氨基酸序列转换为one-hot编码的张量。这个张量将作为神经网络的输入。

        label_tensor = None  # 初始化标签张量为None
        # 当labels_data不为None时，才处理标签数据
        if self.labels_data is not None:
            label = self.labels_data[self.labels_data['PDB_ID'] == pdb_id].iloc[0]['SEC_STRUCT']
            label_tensor = self.label_to_tensor(label)  # 将二级结构标签转换为张量


        pssm_path = f"{self.pssm_folder}/{pdb_id}_train.csv"  # 构建PSSM文件的路径
        # 读取PSSM文件，将其加载为一个DataFrame。PSSM文件包含了每个氨基酸在蛋白质序列中特定位置上的保守性得分。
        pssm_df = pd.read_csv(pssm_path)
        # 将PSSM数据（去除了RES_NUM和AMINO_ACID列）转换为浮点数张量。这个张量也将作为模型的输入之一。        
        pssm_tensor = torch.tensor(pssm_df.drop(columns=['RES_NUM', 'AMINO_ACID']).values, dtype=torch.float32)

        # 根据是否有label_tensor返回相应的数据
        if label_tensor is not None:
            return seq_tensor, label_tensor, pssm_tensor
        else:
            return seq_tensor, pssm_tensor

    def sequence_to_tensor(self, sequence):
        """
        将氨基酸序列转换为one-hot编码的张量
        :param sequence: 氨基酸序列
        :type sequence: 
        :return: 
        :rtype: 
        """
        # 将20种标准氨基酸映射到一个索引上
        aa_to_idx = {aa: idx for idx, aa in enumerate('ACDEFGHIKLMNPQRSTVWY')}
        # 创建一个张量，其形状为（序列长度，氨基酸数量），并将所有元素初始化为0
        tensor = torch.zeros(len(sequence), len(aa_to_idx))
        # 遍历序列中的每个氨基酸，使用aa_to_idx找到对应的索引，并在张量的相应位置填充1，完成one-hot编码
        for i, aa in enumerate(sequence):
            if aa in aa_to_idx:
                tensor[i, aa_to_idx[aa]] = 1
        return tensor

    def label_to_tensor(self, label):
        """
        将二级结构标签序列转换为张量
        :param label: 
        :type label: 
        :return: 
        :rtype: 
        """
        # 将三种二级结构标签（H, E, C）映射到一个整数索引上。
        label_to_idx = {'H': 0, 'E': 1, 'C': 2}
        # 遍历标签字符串中的每个字符，使用label_to_idx找到对应的索引，并将这些索引转换为一个长整型（torch.long）张量。
        tensor = torch.tensor([label_to_idx[label_char] for label_char in label], dtype=torch.long)
        return tensor

In [10]:
def get_data_loaders(batch_size):
    """
    创建训练和验证数据加载器
    :param batch_size: 
    :type batch_size: 
    :return: 
    :rtype: 
    """
    # 路径
    # seqs_path = 'deep-learning-for-msc-202324/seqs_train.csv'
    # labels_path = 'deep-learning-for-msc-202324/labels_train.csv'
    # pssm_folder = 'deep-learning-for-msc-202324/train'
    seqs_path ='E:\Study in the UK\semester 2\Deep Learning\Coursework\deep-learning-for-msc-202324\seqs_train.csv'
    labels_path = 'E:\Study in the UK\semester 2\Deep Learning\Coursework\deep-learning-for-msc-202324\labels_train.csv'
    pssm_folder = 'E:\Study in the UK\semester 2\Deep Learning\Coursework\deep-learning-for-msc-202324\\train'

    # 加载序列数据并生成PDB_ID列表
    seqs_data = pd.read_csv(seqs_path)
    pdb_ids = seqs_data['PDB_ID'].tolist()

    # 分割PDB_ID列表为训练集和验证集
    pdb_ids_train, pdb_ids_val = train_test_split(pdb_ids, test_size=0.2, random_state=42)

    # 创建训练和验证数据集实例
    dataset_train = ProteinDatasetWithPSSM(seqs_path, labels_path, pssm_folder, pdb_ids_train)
    dataset_val = ProteinDatasetWithPSSM(seqs_path, labels_path, pssm_folder, pdb_ids_val)

    # 为训练集和验证集创建DataLoader
    dataloader_train = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn_with_pssm)
    dataloader_val = DataLoader(dataset_val, batch_size=batch_size, shuffle=False, collate_fn=collate_fn_with_pssm)

    return dataloader_train, dataloader_val

In [11]:
# def print_info(dataloader, dataset):
#     first_batch = next(iter(dataloader))
#     sequences_padded, labels_padded, pssms_padded = first_batch
#     print("Sequence tensor shape:", sequences_padded.shape)
#     print("Label tensor shape:", labels_padded.shape)
#     print("PSSM tensor shape:", pssms_padded.shape)
#     print("len(dataloader):", len(dataloader))
#     print("len(dataset):", len(dataset))

In [12]:
# print_info(dataloader_train, dataset_train)

In [13]:
# print_info(dataloader_val, dataset_val)

In [14]:
# print_info(dataloader_test, dataset_test)

# 3.模型设计(Fully Convolutional Networks, FCN)
设计一个FCN模型，该模型仅包含卷积层和激活函数，不使用全连接层（即线性层）。
考虑蛋白质序列的一维性质，使用适当的卷积核（kernels）和窗口（windows）大小来处理序列数据，不需要图像处理中常见的上下采样（up-sampling/down-sampling）。
设计模型架构以使输入PSSM或序列数据经过多个卷积层处理后，输出对应于每个氨基酸残基的H/E/C标签序列。


In [15]:
class ProteinSecondaryStructureFCN(nn.Module):
    """
    用于蛋白质二级结构预测的全卷积网络模型
    """
    def __init__(self, num_layers=1, dropout_rate=0.5):
        
        super(ProteinSecondaryStructureFCN, self).__init__()
        
        # 输入的one-hot编码维度为20（20种氨基酸），PSSM得分维度为20
        input_channels = 20 + 20
        self.layers = nn.ModuleList([
            nn.Conv1d(input_channels, 64, kernel_size=3, padding=1),
            nn.BatchNorm1d(64),
            nn.ReLU(), 
            nn.Dropout(dropout_rate)
        ])
        # 根据num_layers添加隐藏层
        for _ in range(num_layers):
            self.layers.extend([
                nn.Conv1d(64, 64, kernel_size=3, padding=1),
                nn.BatchNorm1d(64),
                nn.ReLU(),
                nn.Dropout(dropout_rate)
            ])
        self.layers.extend([
            nn.Conv1d(64, 128, kernel_size=3, padding=1),
            nn.BatchNorm1d(128),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Conv1d(128, 64, kernel_size=3, padding=1),
            nn.BatchNorm1d(64),
            nn.ReLU(),
            nn.Dropout(dropout_rate),
            nn.Conv1d(64, 3, kernel_size=3, padding=1)
        ])
        
        # # 假设输入的one-hot编码维度为20（20种氨基酸），PSSM得分维度为20
        # input_channels = 20 + 20  # 氨基酸one-hot编码 + PSSM得分
        # # 定义第一个卷积层，输入通道为40（序列的20维one-hot编码 + 20维PSSM数据），输出通道为64，卷积核大小为3, padding=1
        # self.conv1 = nn.Conv1d(input_channels, 64, kernel_size=3, padding=1)
        # self.bn1 = nn.BatchNorm1d(64)  # 添加批量归一化层
        # # self.dropout1 = nn.Dropout(dropout_rate)  # 添加Dropout层
        # 
        # # 定义第二个卷积层，输入通道为64（上一层的输出），输出通道为128，卷积核大小为3
        # self.conv2 = nn.Conv1d(64, 128, kernel_size=3, padding=1)
        # self.bn2 = nn.BatchNorm1d(128)  # 添加批量归一化层
        # # self.dropout2 = nn.Dropout(dropout_rate)  # 添加Dropout层
        # 
        # # 定义第三个卷积层，输入通道为128，输出通道为64，卷积核大小为3
        # self.conv3 = nn.Conv1d(128, 64, kernel_size=3, padding=1)
        # self.bn3 = nn.BatchNorm1d(64)  # 添加批量归一化层
        # # self.dropout3 = nn.Dropout(dropout_rate)  # 添加Dropout层
        # 
        # # 最终输出3个通道，分别对应H, E, C三种二级结构
        # self.conv4 = nn.Conv1d(64, 3, kernel_size=3, padding=1)

    def forward(self, x):
        """
        定义模型的前向传播过程
        :param x: 输入张量
        :return: 模型预测的二级结构标签概率分布
        """
        # x的形状：[batch_size, seq_len, features]
        # 转换x的形状以适配Conv1d：[batch_size, features, seq_len]
        x = x.permute(0, 2, 1)
        
        # # 通过卷积层
        # x = F.relu(self.bn1(self.conv1(x)))
        # # x = self.dropout1(x)
        # 
        # x = F.relu(self.bn2(self.conv2(x)))
        # # x = self.dropout2(x)
        # 
        # x = F.relu(self.bn3(self.conv3(x)))
        # # x = self.dropout3(x)
        # 
        # x = self.conv4(x)

        for layer in self.layers:
            x = layer(x)        
        
        # 转换输出形状以适配后续处理：[batch_size, seq_len, channels]
        x = x.permute(0, 2, 1)
        return x

In [16]:
# 示例：初始化模型
model = ProteinSecondaryStructureFCN()
# model = ProteinStructurePredictionModel()
print(model)


ProteinSecondaryStructureFCN(
  (layers): ModuleList(
    (0): Conv1d(40, 64, kernel_size=(3,), stride=(1,), padding=(1,))
    (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): ReLU()
    (3): Dropout(p=0.5, inplace=False)
    (4): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,))
    (5): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (6): ReLU()
    (7): Dropout(p=0.5, inplace=False)
    (8): Conv1d(64, 128, kernel_size=(3,), stride=(1,), padding=(1,))
    (9): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): ReLU()
    (11): Dropout(p=0.5, inplace=False)
    (12): Conv1d(128, 64, kernel_size=(3,), stride=(1,), padding=(1,))
    (13): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (14): ReLU()
    (15): Dropout(p=0.5, inplace=False)
    (16): Conv1d(64, 3, kernel_size=(3,), stride=(1,), padding=(1,))
  )
)


# 4.模型训练和验证

In [17]:
# def train_and_validate(model, train_loader, val_loader, criterion, optimizer, num_epochs=10):
#     """
#     训练和验证模型
# 
#     本函数负责执行给定模型的训练和验证过程。使用指定的训练数据加载器进行模型训练，并使用验证数据加载器进行性能验证。通过这一过程，模型的参数将得到优化，以改善在验证数据集上的表现。
# 
#     :param model: 要训练和验证的模型对象。
#     :type model: torch.nn.Module
# 
#     :param train_loader: 训练数据加载器，提供模型训练所需的批量数据。
#     :type train_loader: torch.utils.data.DataLoader
# 
#     :param val_loader: 验证数据加载器，提供模型验证所需的批量数据。
#     :type val_loader: torch.utils.data.DataLoader
# 
#     :param criterion: 损失函数，用于评估模型的预测与实际标签之间的差距。
#     :type criterion: torch.nn.modules.loss._Loss
# 
#     :param optimizer: 优化器，负责根据损失函数的反向传播结果更新模型的参数。
#     :type optimizer: torch.optim.Optimizer
# 
#     :param num_epochs: 训练过程中的轮数（epoch数）。
#     :type num_epochs: int
# 
#     :return: 训练和验证过程中的损失历史记录。同时函数执行将导致输入模型的参数根据训练数据进行更新。
#     :rtype: tuple
#     """
#     # train_loss_history = []
#     # val_loss_history = []
#     # train_accuracy_history = []
#     # val_accuracy_history = []
# 
#     for epoch in range(num_epochs):
#         model.train()
#         train_loss, correct_train, total_train = 0.0, 0, 0
#         # 使用tqdm来包装训练数据加载器
#         train_loop = tqdm(train_loader, desc=f'Epoch {epoch+1}/{num_epochs}, Training')
#         for sequences, labels, pssms in train_loop:
#             inputs = torch.cat((sequences, pssms), dim=-1)
#             optimizer.zero_grad()  # 清空之前的梯度
#             outputs = model(inputs)
#             loss = criterion(outputs.reshape(-1, 3), labels.reshape(-1))
#             loss.backward()  # 执行反向传播
#             optimizer.step()  # 更新模型参数
#             train_loss += loss.item() * sequences.size(0)  # 累加每个批次的损失，用于后续计算平均训练损失
#             # 更新tqdm进度条的描述信息
#             train_loop.set_postfix(train_loss=loss.item())
# 
#         #     # 计算准确率
#         #     predicted_labels = outputs.argmax(-1)  # 确保这是[batch_size, seq_len]
#         #     correct_train += (predicted_labels == labels).sum().item()
#         #     total_train += labels.size(0) * labels.size(1)  # 如果labels是[batch_size, seq_len]
#         # 
#         # 
#         # train_loss /= len(train_loader.dataset)  # 计算整个训练数据集的平均损失
#         # train_loss_history.append(train_loss)  # 将平均训练损失添加到历史记录中
#         # avg_train_acc = correct_train / total_train  # 计算整个训练数据集的平均准确率
#         # train_accuracy_history.append(avg_train_acc)  # 将平均训练准确率添加到历史记录中
# 
# 
#         # 验证阶段
#         model.eval()  # 设置模型为评估模式model.eval()，不计算梯度，遍历验证数据集
#         val_loss, correct_val, total_val = 0.0, 0, 0
#         # 使用tqdm来包装验证数据加载器
#         val_loop = tqdm(val_loader, desc=f'Epoch {epoch+1}/{num_epochs}, Validation')
#         with torch.no_grad():  # 在torch.no_grad()上下文中执行验证步骤，避免计算梯度，从而节省计算资源
#             for sequences, labels, pssms in val_loop:
#                 inputs = torch.cat((sequences, pssms), dim=-1)
#                 outputs = model(inputs)
#                 loss = criterion(outputs.reshape(-1, 3), labels.reshape(-1))
#                 val_loss += loss.item() * sequences.size(0)
#                 # 更新tqdm进度条的描述信息
#                 val_loop.set_postfix(val_loss=loss.item())
#         # 
#         #         # 计算准确率
#         #         predicted_labels = outputs.argmax(-1)  # 确保这是[batch_size, seq_len]
#         #         correct_val += (predicted_labels == labels).sum().item()
#         #         total_val += labels.size(0) * labels.size(1)  # 如果labels是[batch_size, seq_len]
#         # 
#         # 
#         # val_loss /= len(val_loader.dataset)
#         # val_loss_history.append(val_loss)  # 将平均验证损失添加到历史记录中
#         # avg_val_acc = correct_val / total_val  # 计算整个验证数据集的平均准确率
#         # val_accuracy_history.append(avg_val_acc)  # 将平均验证准确率添加到历史记录中
#     #     
#     #     print(f'Epoch {epoch+1}/{num_epochs}, Train Loss: {train_loss:.4f}, Train Accuracy: {avg_train_acc:.4f}, Validation Loss: {val_loss:.4f}, Validation Accuracy: {avg_val_acc:.4f}')
#     #     
#     # return train_loss_history, val_loss_history, train_accuracy_history, val_accuracy_history

In [18]:
# def plot_loss_accuracy_history(train_loss_history, val_loss_history, train_accuracy_history, val_accuracy_history):
#     """
#     绘制训练和验证损失及准确率的趋势图。
#     """
#     epochs = range(1, len(train_loss_history) + 1)
# 
#     plt.figure(figsize=(12, 6))
#     plt.subplot(1, 2, 1)
#     plt.plot(epochs, train_loss_history, label='Train Loss')
#     plt.plot(epochs, val_loss_history, label='Validation Loss')
#     plt.title('Loss History')
#     plt.xlabel('Epoch')
#     plt.ylabel('Loss')
#     plt.legend()
# 
#     plt.subplot(1, 2, 2)
#     plt.plot(epochs, train_accuracy_history, label='Train Accuracy')
#     plt.plot(epochs, val_accuracy_history, label='Validation Accuracy')
#     plt.title('Accuracy History')
#     plt.xlabel('Epoch')
#     plt.ylabel('Accuracy')
#     plt.legend()
# 
#     plt.tight_layout()
#     plt.show()

In [19]:
# # 使用前面定义的模型和数据加载器
# model = ProteinSecondaryStructureFCN()
# # 计算损失时，标签中为-1的项将被忽略。这在处理不等长序列或者有填充值的批次数据时非常有用，可以避免填充部分对损失计算的影响。
# criterion = nn.CrossEntropyLoss(ignore_index=-1)
# optimizer = Adam(model.parameters(), lr=0.001)

In [20]:
# train_loss_history, val_loss_history, train_accuracy_history, val_accuracy_history = train_and_validate(model, dataloader_train, dataloader_val, criterion, optimizer)

In [21]:
# plot_loss_accuracy_history(train_loss_history, val_loss_history, train_accuracy_history, val_accuracy_history)

In [22]:
def train_model_with_tune(config, num_epochs=10):
    # 假设你有一个函数 get_data_loaders 来根据 batch_size 获取 DataLoader
    train_loader, val_loader = get_data_loaders(config["batch_size"])
    model = ProteinSecondaryStructureFCN(num_layers=config["num_layers"], dropout_rate=config["dropout_rate"])
    criterion = torch.nn.CrossEntropyLoss(ignore_index=-1)
    optimizer = torch.optim.Adam(model.parameters(), lr=config["lr"])

    for epoch in range(num_epochs):  # 训练10个epoch
        model.train()
        train_loss = 0.0
        correct_train, total_train = 0, 0
        # for batch in train_loader:
        for batch in tqdm(train_loader, desc=f"Training Epoch {epoch+1}/{num_epochs}"):
            sequences, labels = batch[:2]  # 假设batch的前两个元素分别是inputs和labels
            if len(batch) == 3:
                pssms = batch[2]  # 如果有PSSM数据
                # 确保sequences和pssms在最后一个维度（特征维度）上拼接
                inputs = torch.cat((sequences, pssms), dim=-1)  #TODO 拼接序列数据和PSSM数据

            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs.reshape(-1, 3), labels.reshape(-1))
            loss.backward()
            optimizer.step()

            train_loss += loss.item() * inputs.size(0)
            # 计算训练集上的准确率
            _, predicted = torch.max(outputs, 2)
            total_train += labels.numel()
            correct_train += (predicted == labels).sum().item()
        
        # 计算训练集上的平均损失和准确率
        train_loss /= len(train_loader.dataset)
        train_accuracy = correct_train / total_train

        # 评估逻辑
        model.eval()
        val_loss = 0.0
        total, correct = 0, 0
        with torch.no_grad():
            # for batch in val_loader:
            for batch in tqdm(val_loader, desc=f"Validation Epoch {epoch+1}/{num_epochs}"):
                sequences, labels = batch[:2]
                if len(batch) == 3:
                    pssms = batch[2]
                    inputs = torch.cat((sequences, pssms), dim=-1)  # TODO -1?1?

                outputs = model(inputs)
                loss = criterion(outputs.reshape(-1, 3), labels.reshape(-1))
                val_loss += loss.item() * inputs.size(0)

                _, predicted = torch.max(outputs, 2)  # 获取预测结果
                total += labels.numel()
                correct += (predicted == labels).sum().item()

        val_loss /= len(val_loader.dataset)
        val_accuracy = correct / total
        
        # 同时报告训练集和验证集上的损失和准确率给Ray Tune
        # 使用字典形式报告指标
        train.report({
            'train_loss': train_loss,
            'train_accuracy': train_accuracy,
            'val_loss': val_loss,
            'val_accuracy': val_accuracy
        })
        # train.report(train_loss=train_loss, train_accuracy=train_accuracy, val_loss=val_loss, val_accuracy=val_accuracy)

# 5.超参数优化
使用Ray Tune或Ax实现超参数优化，选择合适的超参数（例如，卷积层的数量、卷积核大小、学习率和正则化强度等）来进行优化。
运行超参数优化实验，找到模型性能最优的参数组合，同时考虑到GPU/TPU资源的限制。


In [23]:
# 定义超参数搜索空间
config = {
    "lr": tune.loguniform(1e-4, 1e-1),
    "batch_size": tune.choice([4, 16, 32, 64]),
    "dropout_rate": tune.uniform(0, 0.5),
    "num_layers": tune.choice([0, 1, 2, 3])
}


In [24]:
# 使用ASHA调度器进行试验管理
scheduler = ASHAScheduler(
    metric="val_accuracy",  # 使用验证集准确率作为性能指标
    mode="max",  # 目标是最大化准确率
    max_t=10,  # 最大训练轮数
    grace_period=1,  # 最小训练轮数
    reduction_factor=2  # 减少因子，控制试验减少的速度
)

In [25]:
# 设置CLIReporter以定制输出的信息
reporter = CLIReporter(
    metric_columns=["train_loss", "train_accuracy", "val_loss", "val_accuracy", "training_iteration"]
)

In [26]:
# 启动Ray Tune超参数搜索
result = tune.run(
    train_model_with_tune,
    resources_per_trial={"cpu": 32, "gpu": 1},  # 分配给每个试验的资源
    config=config,
    num_samples=10,  # 每种超参数配置试验的数量
    scheduler=scheduler,
    progress_reporter=reporter,
    local_dir="E:\Study in the UK\semester 2\Deep Learning\Coursework\\ray_results",  # 指定存储试验结果的目录
    name="protein_structure_prediction"  # 指定试验的名称
)


2024-03-16 19:01:39,502	INFO worker.py:1724 -- Started a local Ray instance.
2024-03-16 19:01:42,989	INFO tune.py:220 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2024-03-16 19:01:42,991	INFO tune.py:583 -- [output] This uses the legacy output and progress reporter, as Jupyter notebooks are not supported by the new engine, yet. For more information, please see https://github.com/ray-project/ray/issues/36949


== Status ==
Current time: 2024-03-16 19:01:43 (running for 00:00:00.19)
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8.000: None | Iter 4.000: None | Iter 2.000: None | Iter 1.000: None
Logical resource usage: 0/32 CPUs, 0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: E:/Study in the UK/semester 2/Deep Learning/Coursework/ray_results/protein_structure_prediction
Number of trials: 10/10 (10 PENDING)
+-----------------------------------+----------+-------+--------------+----------------+-------------+--------------+
| Trial name                        | status   | loc   |   batch_size |   dropout_rate |          lr |   num_layers |
|-----------------------------------+----------+-------+--------------+----------------+-------------+--------------|
| train_model_with_tune_a0c08_00000 | PENDING  |       |           32 |      0.365938  | 0.0106089   |            1 |
| train_model_with_tune_a0c08_00001 | PENDING  |       |           16 |      0.137439  | 0.000293754 |            1

Training Epoch 1/10:   7%|▋         | 12/179 [00:03<00:46,  3.61it/s]


== Status ==
Current time: 2024-03-16 19:01:53 (running for 00:00:10.29)
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8.000: None | Iter 4.000: None | Iter 2.000: None | Iter 1.000: None
Logical resource usage: 32.0/32 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: E:/Study in the UK/semester 2/Deep Learning/Coursework/ray_results/protein_structure_prediction
Number of trials: 10/10 (9 PENDING, 1 RUNNING)
+-----------------------------------+----------+-----------------+--------------+----------------+-------------+--------------+
| Trial name                        | status   | loc             |   batch_size |   dropout_rate |          lr |   num_layers |
|-----------------------------------+----------+-----------------+--------------+----------------+-------------+--------------|
| train_model_with_tune_a0c08_00000 | RUNNING  | 127.0.0.1:68380 |           32 |      0.365938  | 0.0106089   |            1 |
| train_model_with_tune_a0c08_00001 | PENDING  |            

Training Epoch 1/10:  17%|█▋        | 30/179 [00:08<00:42,  3.49it/s]


...

== Status ==
Current time: 2024-03-16 19:52:51 (running for 00:51:08.71)
Using AsyncHyperBand: num_stopped=9
Bracket: Iter 8.000: 0.4175767725231936 | Iter 4.000: 0.409628115164778 | Iter 2.000: 0.3333884453052073 | Iter 1.000: 0.257427646836499
Logical resource usage: 32.0/32 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: E:/Study in the UK/semester 2/Deep Learning/Coursework/ray_results/protein_structure_prediction
Number of trials: 10/10 (1 RUNNING, 9 TERMINATED)
+-----------------------------------+------------+-----------------+--------------+----------------+-------------+--------------+--------------+------------------+------------+----------------+----------------------+
| Trial name                        | status     | loc             |   batch_size |   dropout_rate |          lr |   num_layers |   train_loss |   train_accuracy |   val_loss |   val_accuracy |   training_iteration |
|-----------------------------------+------------+-----------------+-------------

Validation Epoch 2/10:  24%|██▍       | 22/90 [00:01<00:04, 16.62it/s]


== Status ==
Current time: 2024-03-16 19:52:56 (running for 00:51:13.72)
Using AsyncHyperBand: num_stopped=9
Bracket: Iter 8.000: 0.4175767725231936 | Iter 4.000: 0.409628115164778 | Iter 2.000: 0.3333884453052073 | Iter 1.000: 0.257427646836499
Logical resource usage: 32.0/32 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: E:/Study in the UK/semester 2/Deep Learning/Coursework/ray_results/protein_structure_prediction
Number of trials: 10/10 (1 RUNNING, 9 TERMINATED)
+-----------------------------------+------------+-----------------+--------------+----------------+-------------+--------------+--------------+------------------+------------+----------------+----------------------+
| Trial name                        | status     | loc             |   batch_size |   dropout_rate |          lr |   num_layers |   train_loss |   train_accuracy |   val_loss |   val_accuracy |   training_iteration |
|-----------------------------------+------------+-----------------+-------------

Validation Epoch 2/10: 100%|██████████| 90/90 [00:05<00:00, 15.71it/s]
2024-03-16 19:53:04,562	INFO tune.py:1042 -- Total run time: 3081.57 seconds (3077.91 seconds for the tuning loop).


== Status ==
Current time: 2024-03-16 19:53:04 (running for 00:51:21.53)
Using AsyncHyperBand: num_stopped=10
Bracket: Iter 8.000: 0.4175767725231936 | Iter 4.000: 0.409628115164778 | Iter 2.000: 0.2681556624555236 | Iter 1.000: 0.257427646836499
Logical resource usage: 32.0/32 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: E:/Study in the UK/semester 2/Deep Learning/Coursework/ray_results/protein_structure_prediction
Number of trials: 10/10 (10 TERMINATED)
+-----------------------------------+------------+-----------------+--------------+----------------+-------------+--------------+--------------+------------------+------------+----------------+----------------------+
| Trial name                        | status     | loc             |   batch_size |   dropout_rate |          lr |   num_layers |   train_loss |   train_accuracy |   val_loss |   val_accuracy |   training_iteration |
|-----------------------------------+------------+-----------------+--------------+-------

In [27]:
# 找到并报告最佳试验
best_trial = result.get_best_trial("val_accuracy", "max", "last")

In [28]:
print("Best trial config: {}".format(best_trial.config))
print("Best trial final validation accuracy: {}".format(best_trial.last_result["val_accuracy"]))

Best trial config: {'lr': 0.000980536827356738, 'batch_size': 4, 'dropout_rate': 0.09819629325261348, 'num_layers': 1}
Best trial final validation accuracy: 0.43182853365936186


In [29]:
# from ax import optimize
# import torch
# from torch.utils.data import DataLoader
# # 假设ProteinSecondaryStructureFCN和get_data_loaders已定义
# 
# def train_evaluate(parameterization):
#     # 根据传入的超参数配置DataLoader
#     train_loader, val_loader = get_data_loaders(parameterization["batch_size"])
# 
#     # 初始化模型
#     model = ProteinSecondaryStructureFCN(num_layers=parameterization["num_layers"], dropout_rate=parameterization["dropout_rate"])
#     criterion = torch.nn.CrossEntropyLoss()
#     optimizer = torch.optim.Adam(model.parameters(), lr=parameterization["lr"])
# 
#     # 这里添加模型的训练和验证代码，计算验证集上的损失或准确率等性能指标
#     # 假设最终性能指标是val_accuracy
#     val_accuracy = ...  # 假设这是从验证过程中得到的性能指标
# 
#     # Ax期望返回一个字典，其中包含至少一个性能指标
#     return {"val_accuracy": (val_accuracy, 0.0)}  # 第二个值是指标的标准误差（这里假设为0）


In [30]:
# from ax.service.ax_client import AxClient
# 
# ax_client = AxClient()
# ax_client.create_experiment(
#     name="protein_secondary_structure_optimization",
#     parameters=[
#         {"name": "lr", "type": "range", "bounds": [1e-4, 1e-1], "log_scale": True},
#         {"name": "batch_size", "type": "choice", "values": [16, 32, 64]},
#         {"name": "dropout_rate", "type": "range", "bounds": [0.2, 0.5]},
#         {"name": "num_layers", "type": "choice", "values": [1, 2, 3]}
#     ],
#     objective_name="val_accuracy",
#     minimize=False  # 设置为False因为我们希望最大化准确率
# )
# 
# # 执行超参数搜索
# total_trials = 20  # 定义要执行的试验次数
# for _ in range(total_trials):
#     parameters, trial_index = ax_client.get_next_trial()
#     # 使用当前参数集训练模型并评估性能
#     results = train_evaluate(parameters)
#     # 将结果报告给Ax
#     ax_client.complete_trial(trial_index=trial_index, raw_data=results)
# 
# # 获取并打印最佳参数
# best_parameters, values = ax_client.get_best_parameters()
# print("Best Parameters:", best_parameters)


# 6.模型解释(Captum)
使用Captum库来理解模型如何识别不同的二级结构区域，通过特征重要性和激活图分析，来解释哪些输入特征对于预测是重要的。

推理和获取概率输出

In [31]:
from torch.utils.data import DataLoader

# 假设你已经定义了一个适用于测试数据的自定义数据集类
test_seqs_path = 'deep-learning-for-msc-202324/seqs_test.csv'
test_pssm_folder = 'deep-learning-for-msc-202324/test'

# 加载测试序列数据，并生成PDB_ID列表
test_seqs_data = pd.read_csv(test_seqs_path)
test_pdb_ids = test_seqs_data['PDB_ID'].tolist()

# 创建测试数据集实例
dataset_test = ProteinDatasetWithPSSM(test_seqs_path, None, test_pssm_folder, test_pdb_ids)

# 创建DataLoader实例
test_loader = DataLoader(dataset_test, batch_size=4, shuffle=False, collate_fn=collate_fn_with_pssm)


In [32]:
def predict(model, dataloader):
    model.eval()  # 设置模型为评估模式
    predictions = []
    with torch.no_grad():
        for sequences, labels, pssms in dataloader:
            inputs = torch.cat((sequences, pssms), dim=-1)
            outputs = model(inputs, apply_softmax=True)  # 获取概率输出
            predictions.append(outputs)
    return torch.cat(predictions, dim=0)

In [33]:
# 假设 test_loader 是你想要进行预测的数据加载器
predictions = predict(model, test_loader)


FileNotFoundError: [Errno 2] No such file or directory: 'deep-learning-for-msc-202324/test/2AIO_1_A_train.csv'